# Research data management with Python and MongoDB (Part 2)

This notebook show an example processing and example analysis procedure for querying raw data from a MongoDB timeseries collection, processing and analysing it for a specific ZBT case. The following steps are performed

1. Preconfiguration: 
    - import relevant libraries
    - define parameters, names, search strings, etc.
    - load environment variables for MongoDB connection
2. Connect to MongoDB and query data
3. Inspect raw data
4. Sample processing on data subset

### 1. Preconfiguration

In [1]:
# Import relevant libraries
import pandas as pd
import os
import numpy as np
from pymongo import MongoClient, errors
from dotenv import load_dotenv
import chardet
from rich import print
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [2]:
# Define data specific parameters
testbench_name = 'BZ011'
set_id_key = 'Set aktuell'
datetime_key = 'Datum'
database_name = 'rdm_workshop'
collection_name = 'BZ011_Rohdaten'
data_file_path = './data/BZ011_Rohdaten.dat'
datetime_format = "%d.%m.%y %H:%M:%S"
averaging_window = 30

In [3]:
# Load environment variables (from .env file) for MongoDB connection
load_dotenv()
mongodb_user = os.environ.get("MONGODB_USER")
mongodb_password = os.environ.get("MONGODB_PASS")
mongodb_ip = os.environ.get("MONGODB_IP")
# Check that all user variables were provided in file
if not all([mongodb_user, mongodb_password, mongodb_ip]):
    raise ValueError('Environment variables not correctly set.')

### 2. Connect to MongoDB and query data


In [4]:
# MongoDB connection
try:
    client = MongoClient(host=mongodb_ip, port=27017, username=mongodb_user,
                         password=mongodb_password, authSource="admin",
                         directConnection=True)
    # Select database and collection
    db = client[database_name]
    collection = db[collection_name]
    # Fetch all data from MongoDB collection
    cursor = collection.find({})  # Empty filter `{}` fetches all documents
    # Convert to DataFrame and sort by datetime column
    df_full = pd.DataFrame(list(cursor)).sort_values([datetime_key])
except (errors.ServerSelectionTimeoutError, errors.ConnectionFailure):
    print('MongoDB server not available. Read data from test file instead.')
    with open(data_file_path, "rb") as f:
        result = chardet.detect(f.read(100000))  # Analyze first 100KB
        detected_encoding = result["encoding"]
    df_full = pd.read_csv(data_file_path, delimiter="\t", encoding=detected_encoding,
                    decimal=",")
    df_full['Datum'] = pd.to_datetime(df_full['Datum'], format=datetime_format)

### 3. Inspect raw data


In [5]:
# Inspect data
df_full.head()

Datum                                           metadata  \
0 2024-08-05 13:11:02  [{'experiment_type': 'Accelerated stress test'...   
1 2024-08-05 13:11:02  [{'experiment_type': 'Accelerated stress test'...   
2 2024-08-05 13:11:03  [{'experiment_type': 'Accelerated stress test'...   
3 2024-08-05 13:11:04  [{'experiment_type': 'Accelerated stress test'...   
4 2024-08-05 13:11:05  [{'experiment_type': 'Accelerated stress test'...   

   BH_H2O_set_An  MW m_H2O_K   TC 12  fl. Mittelwert U  Ali_1_set  \
0            0.0         0.0  1770.0          0.000536        0.5   
1            0.0         0.0  1770.0          0.000390        0.5   
2            0.0         0.0  1770.0          0.000536        0.5   
3            0.0         0.0  1770.0          0.000634        0.5   
4            0.0         0.0  1770.0          0.000634        0.5   

       Set Kommentar  Summe Luft  T Julabo TC 06  ...  T KW ein (10)  \
0  Initialisierung_0         0.0            23.0  ...           24.2   
1  Initialisierung_0         0.0            23.1  ...           24.2   
2  Initialisierung_0         0.0            23.0  ...           24.2   
3  Initialisierung_0         0.0            23.0  ...           24.2   
4  Initialisierung_0         0.0            23.0  ...           24.4   

   T Soll HB / °C  Alarm Index  Begleitheizung TC 3  Begleith. TC 14  \
0       63.052811          0.0                 24.3             24.3   
1       62.548645          0.0                 24.3             24.0   
2       63.052811          0.0                 24.3             24.3   
3       63.556980          0.0                 24.3             24.3   
4       63.961105          0.0                 24.3             24.3   

   V Luft aus  p Luft aus (AI 12)  LED1  C.Leckage_M  U.Vergleich.Alt_M  
0       -0.43                 0.0   0.0          0.0                0.0  
1       -0.43                 0.0   0.0          0.0                0.0  
2       -0.43                 0.0   0.0          0.0                0.0  
3       -0.42                 0.0   0.0          0.0                0.0  
4       -0.43                 0.0   0.0          0.0                0.0  

[5 rows x 95 columns]

In [6]:
# Inspect column names
print(df_full.columns)

Index(['Datum', 'metadata', 'BH_H2O_set_An', 'MW m_H2O_K', 'TC 12',
       'fl. Mittelwert U', 'Ali_1_set', 'Set Kommentar', 'Summe Luft',
       'T Julabo TC 06', 'T Heizbad / °C', 'T H2O_K', 'Senke U o. I',
       'p Mittel An', 'T_Stack (13)', 'T KW aus (11)', '(AI 6) Spannung Mess',
       'p SDB Luft ein (AI 7)', 'STB KW aus (AI13)', 'U1', 'T_Luft_ein',
       'T STB An aus (AI 14)', 'p_H2_Ali6_aus / bar(a)', 'I.Vergleich.Alt_M',
       'p_Ali_H2_ein/ bar(a) 4', 'MW p Ali Kat aus', 'TC Luft Ein (4)', 'LED6',
       'Stack.A.Leckage_M', 'LED3', 'Set aktuell', 'p KW aus (AI 1)',
       'Heizbad', 'p_H2O_nc', 'LED4', 'TC H2 Ein (8)', 'LED6.1',
       'p Mittel Kat', 'MW m_H2O_A', 'Ali_H2_set_6', 'Pumpstufe',
       'Stack.C.Leckage_M', 'fl. Mittelwert I', 'I.Max_M', 'MW V_Luft_ein',
       'p_H2O_K_nc', 'A.Leckage_M', 'T WT (TC 7)', 'p SDB H2 ein (AI 8)',
       'MW V_H2_ein', 'MW pH2_aus', 'AI 15 Strom Mess', 'I.Med_M',
       'Ali_1_set 4', 'T Mischk. (AI 2)', 'T Vorv. (AI 9)',
       'Kathodenblech (1)', 'T Vorv. (AI 11)', 'T_H2_Ali_6_aus',
       'TC Luft Aus (5)', '_id', 'T STB Kat aus  (AI 16)', 'Spg U / V',
       'RTD (2)', 'I.Vergleich_M', 'U.Vergleich_M', 'p H2 aus (AI 4)',
       'TC H2 aus (9)', 'Summe H2O', 'I.Min_M', 'ROW aktuell', 'Kommentar',
       'T_Ali_H2_ein', 'T_H2O_BH2_An', '(AI 3)', 'LED5', 'Summe H2',
       'p SDB KW ein (AI 5)', 'H2O_BH1_Kat', 'T Mischk. (AI 10)', 'LED2',
       'Strom I / A', 'T_Ali Kat aus', 'p_Luft/bar_ein', 'Ali_1_set 3',
       'T KW ein (10)', 'T Soll HB / °C', 'Alarm Index', 'Begleitheizung TC 3',
       'Begleith. TC 14', 'V Luft aus', 'p Luft aus (AI 12)', 'LED1',
       'C.Leckage_M', 'U.Vergleich.Alt_M'],
      dtype='object')

In [7]:
# Plot some control data for plausibility checks
fig = px.line(df_full, x='Datum', y=['p_Luft/bar_ein', 'T_Luft_ein', 'Set aktuell', 'U1', 'Spg U / V'])
fig.show()

### 4. Sample processing on data subset
Querying the complete dataset might be suitable for small data sets, however for large data sets it might be required to only query and process subsets of the data due to memory limitations of your computer. Therefore we will now query a subset of the previously loaded full dataset.

For this example we will process all data at a cell voltage of 0.6 V. There is a comment column `"Set Kommentar" = "0,6V"` indicating these operating points. 
We could possibly directly filter the data by a range of cell voltage values in the `"Spg U / V"` column:
`collection.find({"Spg U / V":{"$gte":0.59, "$lt":0.62})`
However there we might also catch unwanted data points at other operating modes.

In [9]:
# Two different ways of querying for the same data subset
df_subset = pd.DataFrame(list(collection.find({"Set Kommentar": "0,60V"}))).sort_values([datetime_key])
meta_data = df_subset['metadata']
# Metadata should be dropped, since nested lists in dataframes limit functionality of pandas
df_subset = df_subset.drop(columns=['metadata'])
df_subset.info()
df_subset["Set aktuell"]

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5270 entries, 0 to 5269
Data columns (total 94 columns):
 #   Column                  Non-Null Count  Dtype         
---  ------                  --------------  -----         
 0   Datum                   5270 non-null   datetime64[ns]
 1   BH_H2O_set_An           5270 non-null   float64       
 2   MW m_H2O_K              5270 non-null   float64       
 3   TC 12                   5270 non-null   float64       
 4   fl. Mittelwert U        5270 non-null   float64       
 5   Ali_1_set               5270 non-null   float64       
 6   Set Kommentar           5270 non-null   object        
 7   Summe Luft              5270 non-null   float64       
 8   T Julabo TC 06          5270 non-null   float64       
 9   T Heizbad / °C          5270 non-null   float64       
 10  T H2O_K                 5270 non-null   float64       
 11  Senke U o. I            5270 non-null   float64       
 12  p Mittel An             5270 non-null   float64 

0       13
1       13
2       13
3       13
4       13
        ..
5265    28
5266    28
5267    28
5268    28
5269    28
Name: Set aktuell, Length: 5270, dtype: int64

Now we want to subdivide the data set according to individual continuous operation sections.
Each operation mode is identified by `set_id_key = "Set aktuell"`, however the ids might occur multiple separate times, therefore just grouping by that key is not sufficient and we need further manipulation

In [10]:
# Calculate the difference between subsequent id values and fill NaN values with 0
set_change = df_subset[set_id_key].diff().fillna(0)
# Change data types to integer
set_change = set_change.astype('int')
# Set all non-zero values to 1
set_change[set_change != 0] = 1
# Build the cumulative sum along the rows to count changing operating modes and add to data frame
df_subset['set_count'] = set_change.cumsum()

In [11]:
fig = px.scatter(df_subset, x='Datum', y=['set_count', 'Set aktuell', 'U1', 'Spg U / V'])
fig.show()

The next steps include the core of the data processing:
- Data set is filtered for numeric-only data
- The data frame is grouped according to the previously calculated `set_count` column

Further information: https://pandas.pydata.org/docs/user_guide/groupby.html

In [12]:
# Now group the different sets and apply averaging (last 30 values) individually
grouped_subset = df_subset.select_dtypes(include=np.number).groupby(['set_count'])
grouped_subset.describe()

BH_H2O_set_An                                              \
                  count       mean        std        min        25%   
set_count                                                             
0                1500.0  34.434126   7.948875  14.069329  29.931109   
1                  60.0  25.442906   2.694404  17.927429  23.784550   
2                  61.0  29.031145   3.026506  20.266894  26.828487   
3                  61.0  31.691224   2.694414  21.660978  29.946773   
4                  60.0  25.287645   2.370962  19.153611  23.654945   
5                  60.0  29.927273   3.181891  21.423611  27.700847   
6                  61.0  28.108850   2.597384  20.474360  26.572357   
7                1500.0  28.614862  12.294520   6.836907  17.364049   
8                  61.0  21.777794   2.124111  15.559825  20.335471   
9                  61.0  31.858842   3.724557  21.754417  29.309366   
10                 61.0  27.579339   2.854871  19.948448  25.627424   
11                 61.0  30.187632   2.897116  21.643552  28.138954   
12                 61.0  28.496283   2.780621  20.363279  26.702187   
13                 61.0  29.416910   3.019795  20.558972  27.548178   
14                 36.0  24.007730   0.496421  22.906890  23.716527   
15               1500.0  26.512465  12.219362   6.143470  15.467021   
16                  5.0  20.696923   1.935501  17.660920  20.038776   

                                           MW m_H2O_K             ...  \
                 50%        75%        max      count       mean  ...   
set_count                                                         ...   
0          34.406619  41.344466  46.786224     1500.0  45.521988  ...   
1          25.160114  27.104420  31.237279       60.0  33.833112  ...   
2          29.017633  31.593570  34.554419       61.0  39.966129  ...   
3          31.909775  33.502319  35.534922       61.0  43.159474  ...   
4          25.078645  26.892419  29.926790       60.0  33.833740  ...   
5          29.699069  32.609503  36.079276       60.0  40.720460  ...   
6          27.421759  29.971058  32.786638       61.0  37.870858  ...   
7          27.979559  41.330270  47.217578     1500.0  38.649208  ...   
8          21.513326  23.179942  25.735607       61.0  28.737268  ...   
9          31.877626  34.520620  38.540768       61.0  44.041934  ...   
10         27.415239  29.521810  32.767567       61.0  37.278184  ...   
11         29.785419  32.274942  35.698068       61.0  41.343061  ...   
12         28.281095  30.757141  33.811888       61.0  38.591966  ...   
13         29.159119  31.578400  34.946223       61.0  39.926540  ...   
14         24.071478  24.240298  24.973836       36.0   7.955023  ...   
15         25.027243  38.445577  46.029693     1500.0  35.689580  ...   
16         21.204969  22.275059  22.304890        5.0  24.869321  ...   

          C.Leckage_M      U.Vergleich.Alt_M                                \
                  75%  max             count mean  std  min  25%  50%  75%   
set_count                                                                    
0                 0.0  0.0            1500.0  0.0  0.0  0.0  0.0  0.0  0.0   
1                 0.0  0.0              60.0  0.0  0.0  0.0  0.0  0.0  0.0   
2                 0.0  0.0              61.0  0.0  0.0  0.0  0.0  0.0  0.0   
3                 0.0  0.0              61.0  0.0  0.0  0.0  0.0  0.0  0.0   
4                 0.0  0.0              60.0  0.0  0.0  0.0  0.0  0.0  0.0   
5                 0.0  0.0              60.0  0.0  0.0  0.0  0.0  0.0  0.0   
6                 0.0  0.0              61.0  0.0  0.0  0.0  0.0  0.0  0.0   
7                 0.0  0.0            1500.0  0.0  0.0  0.0  0.0  0.0  0.0   
8                 0.0  0.0              61.0  0.0  0.0  0.0  0.0  0.0  0.0   
9                 0.0  0.0              61.0  0.0  0.0  0.0  0.0  0.0  0.0   
10                0.0  0.0              61.0  0.0  0.0  0.0  0.0  0.0  0.0   
11                0.0  0.0          

The first example is using predefined functionality from pandas only:
- Averaging is performed for the last `averaging_window` values of each group with `tail` method
- Since the build-in functions for groups are always aggregation methods (resolving the groups back to dataframes) another groupby-operation is performed
- Then the `mean` method for averaging the reduced data range in each group is applied

Further information: https://pandas.pydata.org/docs/user_guide/groupby.html

In [16]:
df_averaged = grouped_subset.tail(averaging_window)
df_averaged

BH_H2O_set_An  MW m_H2O_K   TC 12  fl. Mittelwert U  Ali_1_set  \
1470      30.103078   41.548332  1770.0          0.606158      1.930   
1471      30.121708   41.552776  1770.0          0.606401      1.929   
1472      29.633919   41.526226  1770.0          0.606352      1.930   
1473      29.635401   41.477184  1770.0          0.606255      1.931   
1474      29.652191   41.427788  1770.0          0.606401      1.930   
...             ...         ...     ...               ...        ...   
5265      17.660920    9.029157  1770.0          0.710239      1.992   
5266      20.038776   23.207809  1770.0          0.618443      1.978   
5267      21.204969   30.272888  1770.0          0.606158      1.965   
5268      22.275059   30.637175  1770.0          0.605768      1.956   
5269      22.304890   31.199574  1770.0          0.606011      1.950   

      Summe Luft  T Julabo TC 06  T Heizbad / °C  T H2O_K  Senke U o. I  ...  \
1470   53.735038            24.2           69.08     20.0          0.60  ...   
1471   53.772837            24.2           69.06     20.0          0.60  ...   
1472   53.810521            24.3           69.08     20.0          0.60  ...   
1473   53.840727            24.3           69.09     20.0          0.60  ...   
1474   53.878632            24.3           69.14     20.0          0.60  ...   
...          ...             ...             ...      ...           ...  ...   
5265  823.668441            23.8           58.90     20.0          0.65  ...   
5266  823.860165            23.4           59.38     20.0          0.60  ...   
5267  824.244312            23.3           59.15     20.0          0.60  ...   
5268  824.617706            23.3           59.16     20.0          0.60  ...   
5269  825.007617            22.8           59.34     20.0          0.60  ...   

      T Soll HB / °C  Alarm Index  Begleitheizung TC 3  Begleith. TC 14  \
1470       73.847954          0.0                110.3            109.8   
1471       73.868790          0.0                109.7            109.8   
1472       74.191246          0.0                109.7            110.3   
1473       74.214584          0.0                109.7            110.3   
1474       74.139954          0.0                109.8            109.7   
...              ...          ...                  ...              ...   
5265       76.733650          0.0                109.5            109.9   
5266       74.816444          0.0                110.1            110.2   
5267       74.517067          0.0                111.5            110.2   
5268       74.259666          0.0                113.4            110.3   
5269       74.947166          0.0                113.8            110.6   

      V Luft aus  p Luft aus (AI 12)  LED1  C.Leckage_M  U.Vergleich.Alt_M  \
1470        1.65               904.0   0.0          0.0                0.0   
1471        1.99               899.0   0.0          0.0                0.0   
1472        1.66               899.0   0.0          0.0                0.0   
1473        1.49               904.0   0.0          0.0                0.0   
1474        1.60               902.0   0.0          0.0                0.0   
...          ...                 ...   ...          ...                ...   
5265        0.99               962.0   0.0          0.0                0.0   
5266        1.58               951.0   0.0          0.0                0.0   
5267        1.21               935.0   0.0          0.0                0.0   
5268        1.95               926.0   0.0          0.0                0.0   
5269        1.64               921.0   0.0          0.0                0.0   

      set_count  
1470          0  
1471          0  
1472          0  
1473          0  
1474          0  
...         ...  
5265         16  
5266         16  
5267         16  
5268         16  
5269         16  

[485 rows x 92 columns]

In [17]:
df_averaged = grouped_subset.tail(averaging_window).groupby(['set_count']).mean()
df_averaged

BH_H2O_set_An  MW m_H2O_K   TC 12  fl. Mittelwert U  Ali_1_set  \
set_count                                                                   
0              30.111788   41.480554  1770.0          0.606111   1.929767   
1              27.530621   36.824387  1770.0          0.606058   1.936600   
2              31.535497   43.711315  1770.0          0.606065   1.927433   
3              33.814909   46.547909  1770.0          0.606010   1.924867   
4              27.175504   36.609895  1770.0          0.605753   1.933733   
5              32.523970   44.471085  1770.0          0.605633   1.926700   
6              30.224267   41.059005  1770.0          0.605363   1.929367   
7              39.724812   57.895732  1770.0          0.605490   1.904000   
8              23.485426   31.333051  1770.0          0.605252   1.935433   
9              34.919077   48.864422  1770.0          0.605348   1.918067   
10             29.910081   41.017112  1770.0          0.605287   1.925200   
11             32.568921   45.008515  1770.0          0.605114   1.919967   
12             30.771687   42.125431  1770.0          0.605130   1.924533   
13             31.841874   43.635972  1770.0          0.605173   1.923433   
14             24.029524    7.932011  1770.0          0.605488   1.973600   
15             43.515455   64.625021  1770.0          0.606044   1.895967   
16             20.696923   24.869321  1770.0          0.629324   1.968200   

           Summe Luft  T Julabo TC 06  T Heizbad / °C  T H2O_K  Senke U o. I  \
set_count                                                                      
0           54.267823       24.176667       69.214667     20.0          0.60   
1           88.653314       24.560000       66.333667     20.0          0.60   
2          130.003328       23.823333       71.766333     20.0          0.60   
3          171.726995       24.040000       71.739000     20.0          0.60   
4          213.729246       24.536667       68.336333     20.0          0.60   
5          256.619059       24.380000       72.377667     20.0          0.60   
6          299.998205       24.060000       70.541333     20.0          0.60   
7          382.325156       24.650000       67.304333     20.0          0.60   
8          417.850224       23.753333       65.025000     20.0          0.60   
9          459.376826       23.800000       73.013667     20.0          0.60   
10         500.618530       24.153333       69.903000     20.0          0.60   
11         542.720402       23.943333       71.988000     20.0          0.60   
12         584.391325       23.973333       70.745333     20.0          0.60   
13         626.334672       24.413333       71.651000     20.0          0.60   
14         718.229575       23.280000       76.725000     20.0          0.60   
15         805.038639       22.880000       71.489333     20.0          0.60   
16         824.279648       23.320000       59.186000     20.0          0.61   

           ...  T KW ein (10)  T Soll HB / °C  Alarm Index  \
set_count  ...                                               
0          ...      68.313333       74.163907          0.0   
1          ...      65.630000       89.648680          0.0   
2          ...      71.146667       89.641916          0.0   
3          ...      70.963333       78.823201          0.0   
4          ...      67.726667       89.720674          0.0   
5          ...      71.653333       87.461848          0.0   
6          ...      69.896667       88.451762          0.0   
7          ...      69.210000       68.213140          0.0   
8          ...      64.286667       89.948950          0.0   
9          ...      72.393333       85.894242          0.0   
10         ...      69.270000       88.777028          0.0   
11         ...      71.336667       85.938606          0.0   
12         ...      70.046667       87.798241          0.0   
13         ...      70.986667       86.767255          0.0   
14         ...      78.440000     

Here a general method is shown if the operations become more complex and involve more steps
- The `apply` method of the GroupBy-objects is used to perform operations on all groups in a single command. Complex operations involving more processing steps for each group can be defined in a separate function, to be passed to the `apply` method. Here a lambda-function is sufficient to define the function (lambda function: anonymous function without explicit naming for use only in a single place). Within the lambda-function:

    - Averaging is performed for the last `averaging_window` values of each group with ´tail´ method, or if the group is smaller then for the last (length_of_group - 2) datapoints to remove transitional data points

    - Then the `mean` method for averaging the selected data range in each group is applied again as before

In [18]:
# Perform the averaging using the apply method for all groups
df_averaged = grouped_subset.apply(
    lambda x: x.tail(min(averaging_window, len(x) - 2)).mean(), include_groups=False, )
df_averaged.reset_index(inplace=True)
df_averaged

set_count  BH_H2O_set_An  MW m_H2O_K   TC 12  fl. Mittelwert U  Ali_1_set  \
0           0      30.111788   41.480554  1770.0          0.606111   1.929767   
1           1      27.530621   36.824387  1770.0          0.606058   1.936600   
2           2      31.535497   43.711315  1770.0          0.606065   1.927433   
3           3      33.814909   46.547909  1770.0          0.606010   1.924867   
4           4      27.175504   36.609895  1770.0          0.605753   1.933733   
5           5      32.523970   44.471085  1770.0          0.605633   1.926700   
6           6      30.224267   41.059005  1770.0          0.605363   1.929367   
7           7      39.724812   57.895732  1770.0          0.605490   1.904000   
8           8      23.485426   31.333052  1770.0          0.605252   1.935433   
9           9      34.919077   48.864422  1770.0          0.605348   1.918067   
10         10      29.910081   41.017111  1770.0          0.605287   1.925200   
11         11      32.568921   45.008515  1770.0          0.605114   1.919967   
12         12      30.771687   42.125431  1770.0          0.605130   1.924533   
13         13      31.841874   43.635972  1770.0          0.605173   1.923433   
14         14      24.029524    7.932011  1770.0          0.605488   1.973600   
15         15      43.515455   64.625021  1770.0          0.606044   1.895967   
16         16      21.928306   30.703212  1770.0          0.605979   1.957000   

    Summe Luft  T Julabo TC 06  T Heizbad / °C  T H2O_K  ...  T KW ein (10)  \
0    54.267823       24.176667       69.214667     20.0  ...      68.313333   
1    88.653314       24.560000       66.333667     20.0  ...      65.630000   
2   130.003328       23.823333       71.766333     20.0  ...      71.146667   
3   171.726995       24.040000       71.739000     20.0  ...      70.963333   
4   213.729247       24.536667       68.336333     20.0  ...      67.726667   
5   256.619059       24.380000       72.377667     20.0  ...      71.653333   
6   299.998205       24.060000       70.541333     20.0  ...      69.896667   
7   382.325156       24.650000       67.304333     20.0  ...      69.210000   
8   417.850224       23.753333       65.025000     20.0  ...      64.286667   
9   459.376826       23.800000       73.013667     20.0  ...      72.393333   
10  500.618530       24.153333       69.903000     20.0  ...      69.270000   
11  542.720402       23.943333       71.988000     20.0  ...      71.336667   
12  584.391325       23.973333       70.745333     20.0  ...      70.046667   
13  626.334672       24.413333       71.651000     20.0  ...      70.986667   
14  718.229575       23.280000       76.725000     20.0  ...      78.440000   
15  805.038639       22.880000       71.489333     20.0  ...      72.970000   
16  824.623212       23.133333       59.216667     20.0  ...      59.100000   

    T Soll HB / °C  Alarm Index  Begleitheizung TC 3  Begleith. TC 14  \
0        74.163907          0.0           109.853333       109.700000   
1        89.648680          0.0           110.120000       110.056667   
2        89.641916          0.0           110.180000       110.110000   
3        78.823201          0.0           110.146667       110.010000   
4        89.720674          0.0           110.163333       110.036667   
5        87.461848          0.0           110.173333       110.070000   
6        88.451762          0.0           110.033333       109.953333   
7        68.213140          0.0           109.863333       110.243333   
8        89.948950          0.0           110.160000       109.926667   
9        85.894242          0.0           110.166667       110.080000   
10       88.777028          0.0           110.130000       110.000000   
11       85.938606          0.0           110.013333       109.996667   
12       87.798241          0.0           110.123333       109.913333   
13       86.767255          0.0           110.106667       110.036667   
14       76.177178         

In [19]:
# More plotting functionality with plotly graph objects instead of plotly express
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(go.Scatter(x=df_averaged['set_count'], y=df_averaged['U1'], name="Voltage"),
              secondary_y=False)

fig.add_trace(go.Scatter(x=df_averaged['set_count'], y=df_averaged['Strom I / A'], name="Current"),
              secondary_y=True)

# Add figure title
fig.update_layout(title_text="Double Y Axis Example")

# Set x-axis title
fig.update_xaxes(title_text="Set Count")

# Set y-axes titles
fig.update_yaxes(title_text="Voltage / V", secondary_y=False)
fig.update_yaxes(title_text="Current / A", secondary_y=True)

fig.show()

Now we do a processing where we want to add the processed data into the initial data frame, and fill all averaged rows with its averaged values. Here, we replace the previous `apply` method with the `transform` method to recover the original data frame shape. Further information: https://pandas.pydata.org/docs/user_guide/groupby.html#the-transform-method

In [20]:
# Perform the averaging using the apply method for all groups
df_averaged = grouped_subset.apply(
    lambda x: x.tail(min(averaging_window, len(x) - 2)).mean(), include_groups=False, )
#df_averaged.reset_index(inplace=True)

# Rename the averaged columns
column_dict = {col: col + '_avg' for col in df_averaged.columns}
df_averaged.rename(columns=column_dict, inplace=True)
new_columns = df_averaged.columns
df_averaged
# df_averaged.set_index(['set_count'], inplace=True)
# df_averaged

BH_H2O_set_An_avg  MW m_H2O_K_avg  TC 12_avg  fl. Mittelwert U_avg  \
set_count                                                                       
0                  30.111788       41.480554     1770.0              0.606111   
1                  27.530621       36.824387     1770.0              0.606058   
2                  31.535497       43.711315     1770.0              0.606065   
3                  33.814909       46.547909     1770.0              0.606010   
4                  27.175504       36.609895     1770.0              0.605753   
5                  32.523970       44.471085     1770.0              0.605633   
6                  30.224267       41.059005     1770.0              0.605363   
7                  39.724812       57.895732     1770.0              0.605490   
8                  23.485426       31.333052     1770.0              0.605252   
9                  34.919077       48.864422     1770.0              0.605348   
10                 29.910081       41.017111     1770.0              0.605287   
11                 32.568921       45.008515     1770.0              0.605114   
12                 30.771687       42.125431     1770.0              0.605130   
13                 31.841874       43.635972     1770.0              0.605173   
14                 24.029524        7.932011     1770.0              0.605488   
15                 43.515455       64.625021     1770.0              0.606044   
16                 21.928306       30.703212     1770.0              0.605979   

           Ali_1_set_avg  Summe Luft_avg  T Julabo TC 06_avg  \
set_count                                                      
0               1.929767       54.267823           24.176667   
1               1.936600       88.653314           24.560000   
2               1.927433      130.003328           23.823333   
3               1.924867      171.726995           24.040000   
4               1.933733      213.729247           24.536667   
5               1.926700      256.619059           24.380000   
6               1.929367      299.998205           24.060000   
7               1.904000      382.325156           24.650000   
8               1.935433      417.850224           23.753333   
9               1.918067      459.376826           23.800000   
10              1.925200      500.618530           24.153333   
11              1.919967      542.720402           23.943333   
12              1.924533      584.391325           23.973333   
13              1.923433      626.334672           24.413333   
14              1.973600      718.229575           23.280000   
15              1.895967      805.038639           22.880000   
16              1.957000      824.623212           23.133333   

           T Heizbad / °C_avg  T H2O_K_avg  Senke U o. I_avg  ...  \
set_count                                                     ...   
0                   69.214667         20.0               0.6  ...   
1                   66.333667         20.0               0.6  ...   
2                   71.766333         20.0               0.6  ...   
3                   71.739000         20.0               0.6  ...   
4                   68.336333         20.0               0.6  ...   
5                   72.377667         20.0               0.6  ...   
6                   70.541333         20.0               0.6  ...   
7                   67.304333         20.0               0.6  ...   
8                   65.025000         20.0               0.6  ...   
9                   73.013667         20.0               0.6  ...   
10                  69.903000         20.0               0.6  ...   
11                  71.988000         20.0               0.6  ...   
12                  70.745333         20.0               0.6  ...   
13                  71.651000         20.0               0.6  ...   
14                  76.725000         20.0               0.6  ...   
15                  71.489333         20.0               0.6  ...   
16          

In [22]:
# Get the last rows of each from the full subset to preserve corresponding index and datetimes
df_last_rows_of_groups = df_subset.groupby(['set_count']).tail(1)
#df_last_rows_of_groups.set_index(['set_count'], inplace=True)
df_last_rows_of_groups.reset_index(inplace=True)
df_last_rows_of_groups.set_index(['set_count'], inplace=True)
df_last_rows_of_groups = df_last_rows_of_groups.drop(columns=list(column_dict.keys()))

df_combined_averaged = pd.concat([df_last_rows_of_groups, df_averaged], axis=1)
# df_average = pd.concat([df_last_rows_of_groups, df_averaged], axis=1)
df_combined_averaged.set_index('index', inplace=True)
df_combined_averaged

Datum Set Kommentar                       _id  \
index                                                               
1499  2024-08-05 14:11:12         0,60V  67d199eb8850920d6db39bcb   
1559  2024-08-05 14:28:35         0,60V  67d199eb8850920d6db39c47   
1620  2024-08-05 14:46:15         0,60V  67d199eb8850920d6db39cca   
1681  2024-08-05 15:03:45         0,60V  67d199eb8850920d6db39d4a   
1741  2024-08-05 15:21:15         0,60V  67d199eb8850920d6db39db6   
1801  2024-08-05 15:38:45         0,60V  67d199eb8850920d6db39e30   
1862  2024-08-05 15:56:25         0,60V  67d199eb8850920d6db39eb3   
3362  2024-08-05 17:52:45         0,60V  67d199eb8850920d6db3a6f6   
3423  2024-08-05 18:10:15         0,60V  67d199eb8850920d6db3a77a   
3484  2024-08-05 18:27:45         0,60V  67d199eb8850920d6db3a7fb   
3545  2024-08-05 18:45:15         0,60V  67d199eb8850920d6db3a871   
3606  2024-08-05 19:02:55         0,60V  67d199eb8850920d6db3a8e6   
3667  2024-08-05 19:20:25         0,60V  67d199eb8850920d6db3a963   
3728  2024-08-05 19:37:55         0,60V  67d199eb8850920d6db3a9e4   
3764  2024-08-05 21:50:30         0,60V  67d199eb8850920d6db3adae   
5264  2024-08-05 23:51:45         0,60V  67d199eb8850920d6db3b658   
5269  2024-08-05 23:59:55         0,60V  67d199eb8850920d6db3b6a6   

       BH_H2O_set_An_avg  MW m_H2O_K_avg  TC 12_avg  fl. Mittelwert U_avg  \
index                                                                       
1499           30.111788       41.480554     1770.0              0.606111   
1559           27.530621       36.824387     1770.0              0.606058   
1620           31.535497       43.711315     1770.0              0.606065   
1681           33.814909       46.547909     1770.0              0.606010   
1741           27.175504       36.609895     1770.0              0.605753   
1801           32.523970       44.471085     1770.0              0.605633   
1862           30.224267       41.059005     1770.0              0.605363   
3362           39.724812       57.895732     1770.0              0.605490   
3423           23.485426       31.333052     1770.0              0.605252   
3484           34.919077       48.864422     1770.0              0.605348   
3545           29.910081       41.017111     1770.0              0.605287   
3606           32.568921       45.008515     1770.0              0.605114   
3667           30.771687       42.125431     1770.0              0.605130   
3728           31.841874       43.635972     1770.0              0.605173   
3764           24.029524        7.932011     1770.0              0.605488   
5264           43.515455       64.625021     1770.0              0.606044   
5269           21.928306       30.703212     1770.0              0.605979   

       Ali_1_set_avg  Summe Luft_avg  T Julabo TC 06_avg  ...  \
index                                                     ...   
1499        1.929767       54.267823           24.176667  ...   
1559        1.936600       88.653314           24.560000  ...   
1620        1.927433      130.003328           23.823333  ...   
1681        1.924867      171.726995           24.040000  ...   
1741        1.933733      213.729247           24.536667  ...   
1801        1.926700      256.619059           24.380000  ...   
1862        1.929367      299.998205           24.060000  ...   
3362        1.904000      382.325156           24.650000  ...   
3423        1.935433      417.850224           23.753333  ...   
3484        1.918067      459.376826           23.800000  ...   
3545        1.925200      500.618530           24.153333  ...   
3606        1.919967      542.720402           23.943333  ...   
3667        1.924533      584.391325           23.973333  ...   
3728        1.923433      626.334672           24.413333  ...   
3764        1.973600      718.229575           23.280000  ...   
5264        1.895967      805.038639           22.880000  ...   
5269        1.957000      824.623212           23.133333  ...   

       T

In [24]:
# Combine the initial data frame (subset) with the averaged data frame 
df_subset_extended = pd.merge(df_subset, df_combined_averaged, how='outer')
df_subset_extended 

Datum  BH_H2O_set_An  MW m_H2O_K   TC 12  fl. Mittelwert U  \
0    2024-08-05 13:46:13      14.070032   12.761551  1770.0          0.716430   
1    2024-08-05 13:46:14      14.069329   12.853262  1770.0          0.698490   
2    2024-08-05 13:46:15      14.943166   12.925468  1770.0          0.679965   
3    2024-08-05 13:46:16      14.924773   13.020681  1770.0          0.661489   
4    2024-08-05 13:46:17      15.307748   13.341151  1770.0          0.643159   
...                  ...            ...         ...     ...               ...   
5265 2024-08-05 23:59:19      17.660920    9.029157  1770.0          0.710239   
5266 2024-08-05 23:59:25      20.038776   23.207809  1770.0          0.618443   
5267 2024-08-05 23:59:35      21.204969   30.272888  1770.0          0.606158   
5268 2024-08-05 23:59:45      22.275059   30.637175  1770.0          0.605768   
5269 2024-08-05 23:59:55      22.304890   31.199574  1770.0          0.606011   

      Ali_1_set Set Kommentar  Summe Luft  T Julabo TC 06  T Heizbad / °C  \
0         1.940         0,60V    5.976036            24.1           69.38   
1         1.940         0,60V    5.996837            24.1           69.41   
2         1.943         0,60V    6.017092            23.8           69.42   
3         1.942         0,60V    6.042240            23.8           69.47   
4         1.942         0,60V    6.062929            23.8           69.53   
...         ...           ...         ...             ...             ...   
5265      1.992         0,60V  823.668441            23.8           58.90   
5266      1.978         0,60V  823.860165            23.4           59.38   
5267      1.965         0,60V  824.244312            23.3           59.15   
5268      1.956         0,60V  824.617706            23.3           59.16   
5269      1.950         0,60V  825.007617            22.8           59.34   

      ...  T KW ein (10)_avg  T Soll HB / °C_avg  Alarm Index_avg  \
0     ...                NaN                 NaN              NaN   
1     ...                NaN                 NaN              NaN   
2     ...                NaN                 NaN              NaN   
3     ...                NaN                 NaN              NaN   
4     ...                NaN                 NaN              NaN   
...   ...                ...                 ...              ...   
5265  ...                NaN                 NaN              NaN   
5266  ...                NaN                 NaN              NaN   
5267  ...                NaN                 NaN              NaN   
5268  ...                NaN                 NaN              NaN   
5269  ...               59.1           74.574633              0.0   

      Begleitheizung TC 3_avg  Begleith. TC 14_avg  V Luft aus_avg  \
0                         NaN                  NaN             NaN   
1                         NaN                  NaN             NaN   
2                         NaN                  NaN             NaN   
3                         NaN                  NaN             NaN   
4                         NaN                  NaN             NaN   
...                       ...                  ...             ...   
5265                      NaN                  NaN             NaN   
5266                      NaN                  NaN             NaN   
5267                      NaN                  NaN             NaN   
5268                      NaN                  NaN             NaN   
5269                    112.9           110.366667             1.6   

      p Luft aus (AI 12)_avg  LED1_avg  C.Leckage_M_avg  U.Vergleich.Alt_M_avg  
0                        NaN       NaN              NaN                    NaN  
1                        NaN       NaN              NaN                    NaN  
2                        NaN       NaN              NaN                    NaN  
3                        NaN       NaN              NaN                    NaN  
4                        NaN       NaN        

In [25]:
# Plot raw data subset and corresponding averaged
data = df_subset_extended
x_values = data[datetime_key]
columns = ["set_count", 'U1', 'U1_avg']
y_values = [data[i] for i in columns]

modes = ['lines', 'markers', 'markers']
markers = [
    {'size': 1},
    {'size': 5},
    {'size': 10},
]

fig_2 = go.Figure()
for i in range(len(y_values)):
    fig_2.add_trace(go.Scatter(x=x_values, y=y_values[i], mode=modes[i],
                               marker=markers[i], name=columns[i]))
    # fig_2.add_trace(go.Scatter(x=x_values, y=data['U1_averaged'],
    #                            mode='markers'))
fig_2.update_layout(
    font_family="Arial",
    font_color="black",
    font_size=14,

)
fig_2.update_xaxes(title="DateTime")
fig_2.update_yaxes(title="Value")
fig_2.show()